Keras Tuner is an easy-to-use, distributable hyperparameter optimization framework that solves the pain points of performing a hyperparameter search. Keras Tuner makes it easy to define a search space and leverage included algorithms to find the best hyperparameter values. Keras Tuner comes with Bayesian Optimization, Hyperband, and Random Search algorithms built-in, and is also designed to be easy for researchers to extend in order to experiment with new search algorithms.

In [1]:
from kerastuner.applications import HyperResNet

In [6]:
from kerastuner.tuners import Hyperband

In [7]:
hypermodel = HyperResNet(input_shape=(128,128,3), classes=10)

In [8]:
tuner  = Hyperband(
    hypermodel,
    objective='val_accuracy',
    max_epochs = 10,
    directory = 'my_dir',
    project_name='Keras tuner')

In [ ]:
tuner.search(x,y, epochs=10, validation_data=(val_x, valy_y))

Here’s a simple end-to-end example. First, we define a model-building function. It takes an hp argument from which you can sample hyperparameters, such as hp.Int('units', min_value=32, max_value=512, step=32) (an integer from a certain range). Notice how the hyperparameters can be defined inline with the model-building code. The example below creates a simple tunable model that we’ll train on CIFAR-10:

# For more info:- https://blog.tensorflow.org/2020/01/hyperparameter-tuning-with-keras-tuner.html

In [12]:
import tensorflow as tf

In [31]:
import tensorflow as tf

def build_model(hp):
  inputs = tf.keras.Input(shape=(32, 32, 3))
  x = inputs
  for i in range(hp.Int('conv_blocks', 3, 5, default=3)):
    filters = hp.Int('filters_' + str(i), 32, 256, step=32)
    for _ in range(2):
      x = tf.keras.layers.Convolution2D(
        filters, kernel_size=(3, 3), padding='same')(x)
      x = tf.keras.layers.BatchNormalization()(x)
      x = tf.keras.layers.ReLU()(x)
    if hp.Choice('pooling_' + str(i), ['avg', 'max']) == 'max':
      x = tf.keras.layers.MaxPool2D()(x)
    else:
      x = tf.keras.layers.AvgPool2D()(x)
  x = tf.keras.layers.GlobalAvgPool2D()(x)
  x = tf.keras.layers.Dense(
      hp.Int('hidden_size', 30, 100, step=10, default=50),
      activation='relu')(x)
  x = tf.keras.layers.Dropout(
      hp.Float('dropout', 0, 0.5, step=0.1, default=0.5))(x)
  outputs = tf.keras.layers.Dense(10, activation='softmax')(x)

  model = tf.keras.Model(inputs, outputs)
  model.compile(
    optimizer=tf.keras.optimizers.Adam(
      hp.Float('learning_rate', 1e-4, 1e-2, sampling='log')),
    loss='sparse_categorical_crossentropy', 
    metrics=['accuracy'])
  return model

In [ ]:
import tensorflow_datasets as tfds

data = tfds.load('cifar10')
train_ds, test_ds = data['train'], data['test']

def standardize_record(record):
  return tf.cast(record['image'], tf.float32) / 255., record['label']

train_ds = train_ds.map(standardize_record).cache().batch(64).shuffle(10000)
test_ds = test_ds.map(standardize_record).cache().batch(64)

tuner.search(train_ds,
             validation_data=test_ds,
             epochs=30,
             callbacks=[tf.keras.callbacks.EarlyStopping(patience=1)])

Each model will train for at most 30 epochs, and two iterations of the Hyperband algorithm will be run. Afterwards, you can retrieve the best models found during the search by using the get_best_models function:

In [ ]:
best_model = tuner.get_best_models(1)[0]

You can also view the optimal hyperparameter values found by the search:

In [ ]:
best_hyperparameters = tuner.get_best_hyperparameters(1)[0]

And that’s all the code that is needed to perform a sophisticated hyperparameter search!

In [ ]:
import kerastuner as kt
import tensorflow as tf
import tensorflow_datasets as tfds


def build_model(hp):
    inputs = tf.keras.Input(shape=(32, 32, 3))
    x = inputs
    for i in range(hp.Int('conv_blocks', 3, 5, default=3)):
        filters = hp.Int('filters_' + str(i), 32, 256, step=32)
        for _ in range(2):
            x = tf.keras.layers.Convolution2D(
              filters, kernel_size=(3, 3), padding='same')(x)
            x = tf.keras.layers.BatchNormalization()(x)
            x = tf.keras.layers.ReLU()(x)
        if hp.Choice('pooling_' + str(i), ['avg', 'max']) == 'max':
            x = tf.keras.layers.MaxPool2D()(x)
        else:
            x = tf.keras.layers.AvgPool2D()(x)
    x = tf.keras.layers.GlobalAvgPool2D()(x)
    x = tf.keras.layers.Dense(
      hp.Int('hidden_size', 30, 100, step=10, default=50),
      activation='relu')(x)
    x = tf.keras.layers.Dropout(
      hp.Float('dropout', 0, 0.5, step=0.1, default=0.5))(x)
    outputs = tf.keras.layers.Dense(10, activation='softmax')(x)

    model = tf.keras.Model(inputs, outputs)
    model.compile(
      optimizer=tf.keras.optimizers.Adam(
        hp.Float('learning_rate', 1e-4, 1e-2, sampling='log')),
      loss='sparse_categorical_crossentropy',
      metrics=['accuracy'])
    return model


tuner = kt.Hyperband(
    build_model,
    objective='val_accuracy',
    max_epochs=30,
    hyperband_iterations=2)

data = tfds.load('cifar10')
train_ds, test_ds = data['train'], data['test']


def standardize_record(record):
    return tf.cast(record['image'], tf.float32) / 255., record['label']


train_ds = train_ds.map(standardize_record).cache().batch(64).shuffle(10000)
test_ds = test_ds.map(standardize_record).cache().batch(64)

tuner.search(train_ds,
             validation_data=test_ds,
             callbacks=[tf.keras.callbacks.EarlyStopping(patience=1)])

best_model = tuner.get_best_models(1)[0]
best_hyperparameters = tuner.get_best_hyperparameters(1)[0]

Epoch 1/2


186/782 [======>.......................] - ETA: 0s - loss: 2.3087 - accuracy: 0.09 - ETA: 2:02 - loss: 2.3212 - accuracy: 0.11 - ETA: 2:29 - loss: 2.2553 - accuracy: 0.15 - ETA: 2:43 - loss: 2.2430 - accuracy: 0.16 - ETA: 2:50 - loss: 2.2161 - accuracy: 0.17 - ETA: 2:56 - loss: 2.2143 - accuracy: 0.17 - ETA: 2:59 - loss: 2.2169 - accuracy: 0.16 - ETA: 3:02 - loss: 2.1986 - accuracy: 0.18 - ETA: 3:04 - loss: 2.1830 - accuracy: 0.19 - ETA: 3:05 - loss: 2.1829 - accuracy: 0.19 - ETA: 3:06 - loss: 2.1737 - accuracy: 0.19 - ETA: 3:07 - loss: 2.1692 - accuracy: 0.19 - ETA: 3:07 - loss: 2.1637 - accuracy: 0.19 - ETA: 3:09 - loss: 2.1567 - accuracy: 0.19 - ETA: 3:10 - loss: 2.1507 - accuracy: 0.20 - ETA: 3:10 - loss: 2.1482 - accuracy: 0.20 - ETA: 3:10 - loss: 2.1378 - accuracy: 0.20 - ETA: 3:11 - loss: 2.1277 - accuracy: 0.21 - ETA: 3:11 - loss: 2.1224 - accuracy: 0.21 - ETA: 3:12 - loss: 2.1172 - accuracy: 0.21 - ETA: 3:12 - loss: 2.1105 - accuracy: 0.21 - ETA: 3:13 - loss: 2.1070 - accuracy

372/782 [=============>................] - ETA: 2:33 - loss: 1.7302 - accuracy: 0.36 - ETA: 2:33 - loss: 1.7282 - accuracy: 0.36 - ETA: 2:33 - loss: 1.7279 - accuracy: 0.36 - ETA: 2:33 - loss: 1.7267 - accuracy: 0.36 - ETA: 2:32 - loss: 1.7256 - accuracy: 0.36 - ETA: 2:32 - loss: 1.7240 - accuracy: 0.36 - ETA: 2:32 - loss: 1.7224 - accuracy: 0.36 - ETA: 2:32 - loss: 1.7220 - accuracy: 0.36 - ETA: 2:31 - loss: 1.7206 - accuracy: 0.36 - ETA: 2:31 - loss: 1.7190 - accuracy: 0.36 - ETA: 2:31 - loss: 1.7177 - accuracy: 0.36 - ETA: 2:31 - loss: 1.7153 - accuracy: 0.36 - ETA: 2:30 - loss: 1.7145 - accuracy: 0.36 - ETA: 2:30 - loss: 1.7135 - accuracy: 0.36 - ETA: 2:30 - loss: 1.7118 - accuracy: 0.36 - ETA: 2:30 - loss: 1.7111 - accuracy: 0.37 - ETA: 2:29 - loss: 1.7095 - accuracy: 0.37 - ETA: 2:29 - loss: 1.7086 - accuracy: 0.37 - ETA: 2:29 - loss: 1.7072 - accuracy: 0.37 - ETA: 2:29 - loss: 1.7061 - accuracy: 0.37 - ETA: 2:28 - loss: 1.7050 - accuracy: 0.37 - ETA: 2:28 - loss: 1.7041 - accura

558/782 [====================>.........] - ETA: 1:46 - loss: 1.5494 - accuracy: 0.43 - ETA: 1:45 - loss: 1.5491 - accuracy: 0.43 - ETA: 1:45 - loss: 1.5484 - accuracy: 0.43 - ETA: 1:45 - loss: 1.5475 - accuracy: 0.43 - ETA: 1:45 - loss: 1.5472 - accuracy: 0.43 - ETA: 1:44 - loss: 1.5461 - accuracy: 0.43 - ETA: 1:44 - loss: 1.5454 - accuracy: 0.43 - ETA: 1:44 - loss: 1.5449 - accuracy: 0.43 - ETA: 1:43 - loss: 1.5440 - accuracy: 0.43 - ETA: 1:43 - loss: 1.5439 - accuracy: 0.43 - ETA: 1:43 - loss: 1.5438 - accuracy: 0.43 - ETA: 1:43 - loss: 1.5433 - accuracy: 0.43 - ETA: 1:42 - loss: 1.5430 - accuracy: 0.43 - ETA: 1:42 - loss: 1.5422 - accuracy: 0.43 - ETA: 1:42 - loss: 1.5412 - accuracy: 0.43 - ETA: 1:42 - loss: 1.5406 - accuracy: 0.43 - ETA: 1:41 - loss: 1.5401 - accuracy: 0.43 - ETA: 1:41 - loss: 1.5392 - accuracy: 0.43 - ETA: 1:41 - loss: 1.5393 - accuracy: 0.43 - ETA: 1:41 - loss: 1.5382 - accuracy: 0.43 - ETA: 1:40 - loss: 1.5376 - accuracy: 0.43 - ETA: 1:40 - loss: 1.5367 - accura

744/782 [===========================>..] - ETA: 57s - loss: 1.4391 - accuracy: 0.476 - ETA: 57s - loss: 1.4384 - accuracy: 0.476 - ETA: 57s - loss: 1.4378 - accuracy: 0.476 - ETA: 57s - loss: 1.4374 - accuracy: 0.476 - ETA: 56s - loss: 1.4366 - accuracy: 0.476 - ETA: 56s - loss: 1.4358 - accuracy: 0.477 - ETA: 56s - loss: 1.4358 - accuracy: 0.477 - ETA: 56s - loss: 1.4354 - accuracy: 0.477 - ETA: 55s - loss: 1.4348 - accuracy: 0.477 - ETA: 55s - loss: 1.4343 - accuracy: 0.477 - ETA: 55s - loss: 1.4337 - accuracy: 0.477 - ETA: 54s - loss: 1.4329 - accuracy: 0.478 - ETA: 54s - loss: 1.4321 - accuracy: 0.478 - ETA: 54s - loss: 1.4318 - accuracy: 0.478 - ETA: 54s - loss: 1.4313 - accuracy: 0.479 - ETA: 53s - loss: 1.4310 - accuracy: 0.479 - ETA: 53s - loss: 1.4306 - accuracy: 0.479 - ETA: 53s - loss: 1.4301 - accuracy: 0.479 - ETA: 53s - loss: 1.4296 - accuracy: 0.479 - ETA: 52s - loss: 1.4290 - accuracy: 0.480 - ETA: 52s - loss: 1.4286 - accuracy: 0.480 - ETA: 52s - loss: 1.4282 - accurac

...

558/782 [====================>.........] - ETA: 1:40 - loss: 1.5840 - accuracy: 0.43 - ETA: 1:39 - loss: 1.5828 - accuracy: 0.43 - ETA: 1:39 - loss: 1.5816 - accuracy: 0.43 - ETA: 1:39 - loss: 1.5803 - accuracy: 0.43 - ETA: 1:39 - loss: 1.5794 - accuracy: 0.43 - ETA: 1:38 - loss: 1.5789 - accuracy: 0.43 - ETA: 1:38 - loss: 1.5782 - accuracy: 0.43 - ETA: 1:38 - loss: 1.5770 - accuracy: 0.43 - ETA: 1:38 - loss: 1.5765 - accuracy: 0.43 - ETA: 1:37 - loss: 1.5750 - accuracy: 0.43 - ETA: 1:37 - loss: 1.5738 - accuracy: 0.43 - ETA: 1:37 - loss: 1.5730 - accuracy: 0.43 - ETA: 1:37 - loss: 1.5719 - accuracy: 0.43 - ETA: 1:36 - loss: 1.5706 - accuracy: 0.43 - ETA: 1:36 - loss: 1.5699 - accuracy: 0.43 - ETA: 1:36 - loss: 1.5690 - accuracy: 0.43 - ETA: 1:36 - loss: 1.5679 - accuracy: 0.43 - ETA: 1:35 - loss: 1.5671 - accuracy: 0.43 - ETA: 1:35 - loss: 1.5663 - accuracy: 0.43 - ETA: 1:35 - loss: 1.5651 - accuracy: 0.44 - ETA: 1:35 - loss: 1.5649 - accuracy: 0.44 - ETA: 1:34 - loss: 1.5646 - accura

744/782 [===========================>..] - ETA: 54s - loss: 1.4511 - accuracy: 0.482 - ETA: 54s - loss: 1.4506 - accuracy: 0.482 - ETA: 54s - loss: 1.4500 - accuracy: 0.482 - ETA: 53s - loss: 1.4497 - accuracy: 0.483 - ETA: 53s - loss: 1.4490 - accuracy: 0.483 - ETA: 53s - loss: 1.4485 - accuracy: 0.483 - ETA: 53s - loss: 1.4482 - accuracy: 0.483 - ETA: 53s - loss: 1.4477 - accuracy: 0.483 - ETA: 52s - loss: 1.4472 - accuracy: 0.484 - ETA: 52s - loss: 1.4465 - accuracy: 0.484 - ETA: 52s - loss: 1.4461 - accuracy: 0.484 - ETA: 52s - loss: 1.4452 - accuracy: 0.484 - ETA: 51s - loss: 1.4445 - accuracy: 0.485 - ETA: 51s - loss: 1.4438 - accuracy: 0.485 - ETA: 51s - loss: 1.4436 - accuracy: 0.485 - ETA: 51s - loss: 1.4432 - accuracy: 0.485 - ETA: 50s - loss: 1.4430 - accuracy: 0.485 - ETA: 50s - loss: 1.4424 - accuracy: 0.485 - ETA: 50s - loss: 1.4422 - accuracy: 0.486 - ETA: 50s - loss: 1.4417 - accuracy: 0.486 - ETA: 49s - loss: 1.4411 - accuracy: 0.486 - ETA: 49s - loss: 1.4408 - accurac

782/782 [==============================] - ETA: 9s - loss: 1.3593 - accuracy: 0.51 - ETA: 8s - loss: 1.3587 - accuracy: 0.51 - ETA: 8s - loss: 1.3582 - accuracy: 0.51 - ETA: 8s - loss: 1.3578 - accuracy: 0.51 - ETA: 8s - loss: 1.3574 - accuracy: 0.51 - ETA: 7s - loss: 1.3571 - accuracy: 0.51 - ETA: 7s - loss: 1.3565 - accuracy: 0.51 - ETA: 7s - loss: 1.3560 - accuracy: 0.51 - ETA: 7s - loss: 1.3554 - accuracy: 0.51 - ETA: 6s - loss: 1.3552 - accuracy: 0.51 - ETA: 6s - loss: 1.3547 - accuracy: 0.51 - ETA: 6s - loss: 1.3542 - accuracy: 0.51 - ETA: 6s - loss: 1.3536 - accuracy: 0.51 - ETA: 5s - loss: 1.3529 - accuracy: 0.51 - ETA: 5s - loss: 1.3524 - accuracy: 0.51 - ETA: 5s - loss: 1.3519 - accuracy: 0.51 - ETA: 5s - loss: 1.3513 - accuracy: 0.51 - ETA: 4s - loss: 1.3511 - accuracy: 0.51 - ETA: 4s - loss: 1.3506 - accuracy: 0.51 - ETA: 4s - loss: 1.3504 - accuracy: 0.51 - ETA: 4s - loss: 1.3502 - accuracy: 0.51 - ETA: 3s - loss: 1.3498 - accuracy: 0.51 - ETA: 3s - loss: 1.3492 - accuracy

186/782 [======>.......................] - ETA: 0s - loss: 0.9822 - accuracy: 0.68 - ETA: 1:34 - loss: 1.0404 - accuracy: 0.64 - ETA: 2:07 - loss: 1.0129 - accuracy: 0.65 - ETA: 2:24 - loss: 1.0089 - accuracy: 0.62 - ETA: 2:33 - loss: 0.9977 - accuracy: 0.63 - ETA: 2:39 - loss: 0.9578 - accuracy: 0.64 - ETA: 2:43 - loss: 0.9843 - accuracy: 0.64 - ETA: 2:46 - loss: 0.9969 - accuracy: 0.64 - ETA: 2:49 - loss: 0.9839 - accuracy: 0.65 - ETA: 2:51 - loss: 0.9818 - accuracy: 0.66 - ETA: 2:52 - loss: 0.9931 - accuracy: 0.66 - ETA: 2:53 - loss: 0.9939 - accuracy: 0.66 - ETA: 2:54 - loss: 1.0193 - accuracy: 0.65 - ETA: 2:55 - loss: 1.0250 - accuracy: 0.65 - ETA: 2:55 - loss: 1.0172 - accuracy: 0.65 - ETA: 2:56 - loss: 1.0189 - accuracy: 0.65 - ETA: 2:56 - loss: 1.0104 - accuracy: 0.65 - ETA: 2:57 - loss: 1.0172 - accuracy: 0.65 - ETA: 2:57 - loss: 1.0027 - accuracy: 0.65 - ETA: 2:57 - loss: 0.9921 - accuracy: 0.66 - ETA: 2:57 - loss: 0.9879 - accuracy: 0.66 - ETA: 2:58 - loss: 0.9927 - accuracy

343/782 [============>.................] - ETA: 2:25 - loss: 0.9799 - accuracy: 0.66 - ETA: 2:25 - loss: 0.9796 - accuracy: 0.66 - ETA: 2:25 - loss: 0.9782 - accuracy: 0.66 - ETA: 2:24 - loss: 0.9776 - accuracy: 0.66 - ETA: 2:24 - loss: 0.9772 - accuracy: 0.66 - ETA: 2:24 - loss: 0.9765 - accuracy: 0.66 - ETA: 2:24 - loss: 0.9766 - accuracy: 0.66 - ETA: 2:23 - loss: 0.9756 - accuracy: 0.66 - ETA: 2:23 - loss: 0.9751 - accuracy: 0.66 - ETA: 2:23 - loss: 0.9744 - accuracy: 0.66 - ETA: 2:23 - loss: 0.9743 - accuracy: 0.66 - ETA: 2:22 - loss: 0.9744 - accuracy: 0.66 - ETA: 2:22 - loss: 0.9744 - accuracy: 0.66 - ETA: 2:22 - loss: 0.9745 - accuracy: 0.66 - ETA: 2:22 - loss: 0.9735 - accuracy: 0.66 - ETA: 2:21 - loss: 0.9735 - accuracy: 0.66 - ETA: 2:21 - loss: 0.9723 - accuracy: 0.66 - ETA: 2:21 - loss: 0.9723 - accuracy: 0.66 - ETA: 2:21 - loss: 0.9719 - accuracy: 0.66 - ETA: 2:20 - loss: 0.9716 - accuracy: 0.66 - ETA: 2:20 - loss: 0.9710 - accuracy: 0.66 - ETA: 2:20 - loss: 0.9704 - accura